In [ ]:
# ..... get cell types using Hill et al markers ..... #

In [2]:
library(SingleCellExperiment)
library(MetaMarkers)
library(Seurat)
library(data.table)
library(dplyr)

In [3]:
# load list of orthologs
om = read.delim('mouse_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'chicken', 'LCA', 'homology_type')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12287     4

mouse  chicken LCA     homology_type   
6 mt-Nd1 ND1     Amniota ortholog_one2one

In [4]:
# get list of samples
stages = c(rep('stage23', 2), rep(c('stage28', 'stage32'), each = 3))
samples = c('sample3', 'sample10', 'sample5', 'sample10', 'sample11',
           'sample5', 'sample10', 'sample12')

In [5]:
# get top markers
get_top_markers <- function(df){
    ctypes = unique(df$cluster)
    marker_df = c()
    
    for(ii in 1:length(ctypes)){
        temp = df[df$cluster==ctypes[ii],]
        temp$group = 'all'
        temp$cell_type = temp$cluster
        
        if(dim(temp)[1]>100){
            marker_df = rbind(marker_df,
                              temp[1:100, c('group', 'cell_type', 'gene', 'avg_logFC', 'p_val_adj')])            
        }else{
            # take as many markers as possible
            marker_df = rbind(marker_df,
                              temp[, c('group', 'cell_type', 'gene', 'avg_logFC', 'p_val_adj')]) 
        }
    }
    return(as_tibble(marker_df))
}

In [6]:
# load markers
markers = read.delim('~/septation/markers/Hill/Hill_markers.csv', sep = ',')
markers$gene <- om$chicken[match(markers$gene, om$mouse)]
markers <- markers[!is.na(markers$gene),]
markers[1:2,]

# tibble of group, cell_type, gene, rank
top_markers = get_top_markers(markers)
top_markers[1:2,]

X    p_val avg_logFC pct.1 pct.2 p_val_adj cluster gene 
2 Rbp4 0     3.561264  1     0.036 0         Hapato  RBP4A
3 Ttr  0     3.033434  1     0.028 0         Hapato  TTR

group cell_type gene  avg_logFC p_val_adj
1 all   Hapato    RBP4A 3.561264  0        
2 all   Hapato    TTR   3.033434  0

In [7]:
# get cell type anno
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(id in 1:length(samples)){
    
    # load seurat object
    sce = readRDS(paste0(stages[id], '_', samples[id], '_data.rds'))

    # get SCE object
    sc3 = SingleCellExperiment(list(counts = sce@assays$RNA@counts))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
    # predict cell type neighborhood
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # save
    write.table(ct_pred, file = paste0('annotations/', stages[id], '_', samples[id], '_Hill_celltypes.csv'),
            sep = ',', row.names = T, col.names = T, quote = F)
    
    setTxtProgressBar(pb, id)
}